In lecture 8 of mcs 320, we consider evaluation and execution.

# 1. Addition and Multiplication Tables

For finite fields, we can tabulate the outcomes of the addition and multiplications of all elements in the field.  Let us make a field with four elements.  Because four is not a prime number, we cannot use the modulo four integers.

In [1]:
Z2 = Integers(2)
P.<x> = Z2[]
q = x^2 + x + 1
factor(q)

x^2 + x + 1

We have a polynomial ``q`` in ``x`` of degree 2 with modulo two coefficients which is irreducible.

In [2]:
Q.<a> = Z2.extension(q)
list(Q)

[0, 1, a, a + 1]

In [3]:
print('the addition table:')
for x in Q:
    print([x+y for y in Q])

the addition table:
[0, 1, a, a + 1]
[1, 0, a + 1, a]
[a, a + 1, 0, 1]
[a + 1, a, 1, 0]


In [4]:
print('the multiplication table:')
for x in Q:
    print([x*y for y in Q])

the multiplication table:
[0, 0, 0, 0]
[0, 1, a, a + 1]
[0, a, a + 1, 1]
[0, a + 1, 1, a]


In ``Q`` we have the following properties:

1. every number has an inverse with respect to the addition,

2. every nonzero number has a multiplicative inverse.

These properties make that ``Q`` is a field.

Observe the addition and multiplication tables of the ``GF(4)`` the Galois field of size 4.

In [5]:
GF(4).addition_table()

+  a b c d
 +--------
a| a b c d
b| b a d c
c| c d a b
d| d c b a


In [6]:
GF(4).multiplication_table()

*  a b c d
 +--------
a| a a a a
b| a b c d
c| a c d b
d| a d b c


# 2. Binary Expression Trees

A binary expression tree is a binary tree with leaves and nodes:

1. The leaves are either constants or operands.

2. The notes are the arithmetical operations.

Let us make an example: $x^3 + 4 x y^3$.

In [7]:
from sage.ext.fast_callable import ExpressionTreeBuilder
etb = ExpressionTreeBuilder(vars=['x','y'])
x = etb.var('x')
y = etb.var('y')
p = x^3 + 4*x*y^3
print(p)

add(ipow(v_0, 3), mul(mul(4, v_0), ipow(v_1, 3)))


To draw the tree, we start with the six leaves.

In [8]:
L1 = LabelledBinaryTree([None, None], label='v_0')
L2 = LabelledBinaryTree([None, None], label='3')
L3 = LabelledBinaryTree([None, None], label='4')
L4 = LabelledBinaryTree([None, None], label='v_1')

Two of the leaves appear twice, we do not make duplicate leaves.

In [9]:
N12 = LabelledBinaryTree([L1, L2], label="*")
ascii_art(N12)

  _*_
 /   \
v_0   3

In [10]:
N31 = LabelledBinaryTree([L3, L1], label='*')
ascii_art(N31)

  *
 / \
4   v_0

In [11]:
N42 = LabelledBinaryTree([L4, L2], label='^')
ascii_art(N42)

  _^_
 /   \
v_1   3

In [12]:
N3142 = LabelledBinaryTree([N31, N42], label="*")
ascii_art(N3142)

    ___*____
   /        \
  *         _^_
 / \       /   \
4   v_0   v_1   3

In [13]:
final= LabelledBinaryTree([N12, N3142], label="+")
ascii_art(final)

     _____+_____
    /           \
  _*_         ___*____
 /   \       /        \
v_0   3     *         _^_
           / \       /   \
          4   v_0   v_1   3

To see a representation of the program listing to evaluate ``p``, we work as follows.

In [14]:
f = fast_callable(p)
f.op_list()

[('load_arg', 0),
 ('ipow', 3),
 ('load_const', 4),
 ('load_arg', 0),
 'mul',
 ('load_arg', 1),
 ('ipow', 3),
 'mul',
 'add',
 'return']